In [1]:
import dash
import numpy as np
import pandas as pd
import plotly as plt
import plotly.express as px
import plotly.graph_objects as go
import psycopg2
from dash import Dash, Input, Output, dcc, html
from dotenv import load_dotenv
from plotly.subplots import make_subplots
from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sqlalchemy import create_engine

import os

load_dotenv()


pd.options.plotting.backend = "plotly"

In [2]:
database_uri = os.environ['DATABASE_URI']
connection = psycopg2.connect(database_uri)

In [3]:
df = pd.read_csv('Telco-Churn.csv')
#in below dict we will store every action, which edited the dataset
taken_actions = dict()

In [4]:
df.describe

<bound method NDFrame.describe of       customerID  gender  SeniorCitizen Partner Dependents  tenure  \
0     7590-VHVEG  Female              0     Yes         No       1   
1     5575-GNVDE    Male              0      No         No      34   
2     3668-QPYBK    Male              0      No         No       2   
3     7795-CFOCW    Male              0      No         No      45   
4     9237-HQITU  Female              0      No         No       2   
...          ...     ...            ...     ...        ...     ...   
7038  6840-RESVB    Male              0     Yes        Yes      24   
7039  2234-XADUH  Female              0     Yes        Yes      72   
7040  4801-JZAZL  Female              0     Yes        Yes      11   
7041  8361-LTMKD    Male              1     Yes         No       4   
7042  3186-AJIEK    Male              0      No         No      66   

     PhoneService     MultipleLines InternetService OnlineSecurity  ...  \
0              No  No phone service             DS

In [5]:
#df.isna().sum()
df['DeviceProtection'].value_counts()

No                     3095
Yes                    2422
No internet service    1526
Name: DeviceProtection, dtype: int64

In [6]:
df['InternetService'].value_counts()

Fiber optic    3096
DSL            2421
No             1526
Name: InternetService, dtype: int64

In [7]:
df['TotalCharges'] = pd.to_numeric(df.TotalCharges, errors='coerce')
taken_actions['1'] = 'changed TotalCharges column from type object to numeric, argument "errors" had been set to "coerce"'
df.dropna(inplace=True)
taken_actions['2'] = 'droped NAs'
for col in df.columns:
    df[col] = df[col].replace(to_replace=' ', value='-', regex=True)
taken_actions['2'] = 'replaced spaces from values of rows to a dash (-)'


In [8]:
#we save the data to a database after cleaning is done
db = create_engine(database_uri)
#with db.connect() as conn:
    #df.to_sql('telco_churn', conn, if_exists='replace')

In [9]:
connection = psycopg2.connect(database_uri)

In [10]:

#pre-create traces
monthly_charges_trace = go.Box(y=df['MonthlyCharges'], name='Monthly Charges')
total_charges_trace = go.Box(y=df['TotalCharges'], name='Total Charges')


# Create figure with secondary y-axis
linear_fig = make_subplots(specs=[[{"secondary_y": True}]])

linear_fig.add_trace(
    monthly_charges_trace,
    secondary_y=False,
)

linear_fig.add_trace(
    total_charges_trace,
    secondary_y=True,
)
#prettify
linear_fig.update_layout(
    showlegend=False,
    width = 900,
    margin = {'t' : 50, 'b': 50}
)
linear_fig.show()

In [11]:
df[['MultipleLines']].value_counts()

# below we have queries to use as CREATE_PHONESERVICE_VIEW's value
# below SQL query sets MultipleLines values as rows's values
# CREATE VIEW phone_service_view AS
# SELECT 
# "MultipleLines", COUNT("MultipleLines")
# FROM telco_churn
# GROUP BY "MultipleLines";

# below a query which sets MultipleLines values as columns, but returns three identical rows,
# CREATE VIEW phone_service_view AS
# SELECT 
# (SELECT COUNT("MultipleLines") AS "Yes" FROM telco_churn WHERE "MultipleLines" = 'Yes'),
# (SELECT COUNT("MultipleLines") AS "No" FROM telco_churn WHERE "MultipleLines" = 'No'),
# (SELECT COUNT("MultipleLines") AS "No_Phone_Service" FROM telco_churn WHERE "MultipleLines" = 'No-phone-service') 
# FROM telco_churn
# GROUP BY "MultipleLines";

MultipleLines   
No                  3385
Yes                 2967
No-phone-service     680
dtype: int64

In [12]:
#now we will make chart of amount of customers using additional services, let's begin from Phone Service
CREATE_PHONESERVICE_VIEW = """CREATE VIEW phone_service_view AS
SELECT 
"MultipleLines", COUNT("MultipleLines")
FROM telco_churn
GROUP BY "MultipleLines";"""
PHONE_SERVICE_VIEW = "SELECT * FROM phone_service_view;"
try:
    with connection:
        with connection.cursor() as cursor:
            cursor.execute(CREATE_PHONESERVICE_VIEW)
except:
    pass
finally: 
    with db.connect() as conn:
        phone_service = pd.read_sql_query(PHONE_SERVICE_VIEW, conn)

#phone_service["Amount-of-users"] = 'Amount of users'
phone_service.sort_values('count', ascending=False, inplace=True)
phone_service

MultipleLines  count
0                No   3385
2               Yes   2967
1  No-phone-service    680

In [13]:
# phone_service_fig = px.bar(phone_service, x='count', y='Amount-of-users',
#                             color='MultipleLines', orientation='h',
#                             height = 250, width=800,
#                             text='MultipleLines',
#                             ) 
# phone_service_fig.layout.update(showlegend=False)                          
# phone_service_trace = [go.Bar(
#         name='No',
#         x=[3385],
#         y=["Multiple Lines"],
#         orientation='h',
#         text='No'),
#     go.Bar(
#         name='Yes',
#         x=[2967],
#         y=["Multiple Lines"],
#         orientation='h',
#         text='Yes'),
#     go.Bar(
#         name='No phone service',
#         x=[680],
#         y=["Multiple Lines"],
#         orientation='h',
#         text='No phone service')
# ]
# fig = go.Figure(data=phone_service_trace)
# fig.update_layout(barmode='stack')
# fig.show()

In [14]:
services_traces = list()
for ind, row in phone_service.iterrows():
    trace = go.Bar(
        name = row['MultipleLines'],
        x=[row['count']],
        y=["Multiple Lines"],
        orientation='h',
        text=row["MultipleLines"], textangle=0
    )
    services_traces.append(trace)


In [15]:
# online_security = df['OnlineSecurity'].value_counts().to_frame()
# online_security.reset_index(inplace=True, names='Service')
# online_security
# for ind, row in online_security.iterrows():
#     trace = go.Bar(
#         name = row['Service'],
#         x=[row['OnlineSecurity']],
#         y=["Service"],
#         orientation='h',
#         text=row["Service"], textangle=0
#     )
#     services_traces.append(trace)


In [16]:
services = df.loc[:, 'DeviceProtection':'StreamingMovies']  # we will iterate through these columns to create traces and append them to a list
for column in services:
    service_count = df[column].value_counts().to_frame() # count yes and no
    service_count.reset_index(inplace=True, names='Service') # we don't want answer as an index
    for ind, row in service_count.iterrows():
        trace = go.Bar(
            name = row['Service'],
            x=[row[column]],
            y=[column],
            orientation='h',
            text=row['Service'], textangle=0
        )
        services_traces.append(trace)


In [17]:
services_fig = go.Figure(data=services_traces)
services_fig.update_traces(width=0.5)
services_fig.update_layout(barmode='stack', width=1100, showlegend=False)
services_fig.show()

In [18]:
# we can see above, that there we have more users who are using our phone services only, than these, who use internet services only

# belowe function will be used to service creation a view and retrieving a view from it
def service_query(creating_query: str, calling_query: str) -> pd.DataFrame():
    try:
        with connection:
            with connection.cursor() as cursor:
                cursor.execute(creating_query)
    except Exception:
        pass
    finally: 
        with db.connect() as conn:
            frame = pd.read_sql_query(calling_query, conn)
    return frame


In [19]:
CREATE_CONTRACT_VIEW = """CREATE VIEW contract_view AS
SELECT
"Contract",
"Churn",
COUNT("Churn")
FROM telco_churn
GROUP BY "Contract", "Churn"
ORDER BY "Contract";"""
CONTRACT_VIEW = "SELECT * FROM contract_view;"
contract_frame = service_query(CREATE_CONTRACT_VIEW, CONTRACT_VIEW)
contract_figure = px.bar(contract_frame, x='Contract', y='count', color='Churn')
contract_figure.show()
# well, this chart doesn't tell us much after all

In [20]:
CREATE_CHARGES_VIEW = """CREATE VIEW charges AS
SELECT 
"MonthlyCharges",
"TotalCharges",
"Churn",
ROUND("TotalCharges"/"MonthlyCharges") AS Months
FROM telco_churn;"""
CHARGES_VIEW = "SELECT * FROM charges;"
charges = service_query(CREATE_CHARGES_VIEW, CHARGES_VIEW)

churn_numeric = pd.get_dummies(charges['Churn'])    
charges['Left'] = churn_numeric['Yes']
charges['Stayed'] = churn_numeric['No']
charges['sum'] = charges['Stayed'].apply(lambda x: 1 if x == 1 else -1 )
charges

MonthlyCharges  TotalCharges Churn  months  Left  Stayed  sum
0              29.85         29.85    No     1.0     0       1    1
1              56.95       1889.50    No    33.0     0       1    1
2              53.85        108.15   Yes     2.0     1       0   -1
3              42.30       1840.75    No    44.0     0       1    1
4              70.70        151.65   Yes     2.0     1       0   -1
...              ...           ...   ...     ...   ...     ...  ...
7027           84.80       1990.50    No    23.0     0       1    1
7028          103.20       7362.90    No    71.0     0       1    1
7029           29.60        346.45    No    12.0     0       1    1
7030           74.40        306.60   Yes     4.0     1       0   -1
7031          105.65       6844.50    No    65.0     0       1    1

[7032 rows x 7 columns]

In [21]:
churn_fig = px.scatter(charges, x='months', y='MonthlyCharges', color='Churn', hover_data=['Churn'])
churn_fig.update_traces(marker_size=3)
churn_fig.update_layout(width=900, margin={'r':45, 'l':35})
churn_fig.show()

In [22]:
charges

MonthlyCharges  TotalCharges Churn  months  Left  Stayed  sum
0              29.85         29.85    No     1.0     0       1    1
1              56.95       1889.50    No    33.0     0       1    1
2              53.85        108.15   Yes     2.0     1       0   -1
3              42.30       1840.75    No    44.0     0       1    1
4              70.70        151.65   Yes     2.0     1       0   -1
...              ...           ...   ...     ...   ...     ...  ...
7027           84.80       1990.50    No    23.0     0       1    1
7028          103.20       7362.90    No    71.0     0       1    1
7029           29.60        346.45    No    12.0     0       1    1
7030           74.40        306.60   Yes     4.0     1       0   -1
7031          105.65       6844.50    No    65.0     0       1    1

[7032 rows x 7 columns]

In [33]:
churn_heatmap = px.density_heatmap(
    charges,
    x='months', y='MonthlyCharges', z="sum",
    color_continuous_scale='viridis',
    histfunc='sum', histnorm='probability',
    nbinsx=8, nbinsy=6,
    width=800,
    range_y = [0, charges['MonthlyCharges'].max()],
    range_x = [0, charges['months'].max()]
)
churn_heatmap.update_layout(width=900, margin={'r':45, 'l':35})
churn_heatmap.show()

In [29]:
charges

MonthlyCharges  TotalCharges Churn  months  Left  Stayed  sum
0              29.85         29.85    No     1.0     0       1    1
1              56.95       1889.50    No    33.0     0       1    1
2              53.85        108.15   Yes     2.0     1       0   -1
3              42.30       1840.75    No    44.0     0       1    1
4              70.70        151.65   Yes     2.0     1       0   -1
...              ...           ...   ...     ...   ...     ...  ...
7027           84.80       1990.50    No    23.0     0       1    1
7028          103.20       7362.90    No    71.0     0       1    1
7029           29.60        346.45    No    12.0     0       1    1
7030           74.40        306.60   Yes     4.0     1       0   -1
7031          105.65       6844.50    No    65.0     0       1    1

[7032 rows x 7 columns]

In [43]:
X_linear = charges.MonthlyCharges.values.reshape(-1, 1)
model = LinearRegression()
model.fit(X_linear, charges['Stayed'])
x_linear_range = np.linspace(X_linear.min(), X_linear.max(), 100)
y_linear_range = model.predict(x_linear_range.reshape(-1, 1))
linear_fig = px.scatter(charges, x='MonthlyCharges', y='Stayed', opacity=0.65)
linear_fig.add_traces(go.Scatter(x=x_linear_range, y=y_linear_range, name='Regression Fit'))
linear_fig.update_layout(width=900, margin={'r':45, 'l':35})
linear_fig.show()

In [34]:
mesh_size = 0.2
margin = 0

X_3D = charges[['months', 'MonthlyCharges']]
Y_3D = charges[['Stayed']]

model = SVR(C=1.)
model.fit(X_3D, Y_3D)
x3d_min, x3d_max = X_3D.months.min() - margin, X_3D.months.max() + margin
y3d_min, y3d_max = X_3D.MonthlyCharges.min() - margin, X_3D.MonthlyCharges.max() + margin
x3d_range = np.arange(x3d_min, x3d_max, mesh_size)
y3d_range = np.arange(y3d_min, y3d_max, mesh_size)
xx3d, yy3d = np.meshgrid(x3d_range, y3d_range)

pred = model.predict(np.c_[xx3d.ravel(), yy3d.ravel()])
pred = pred.reshape(xx3d.shape)

fig_3d = px.scatter_3d(charges, x='months', y='MonthlyCharges', z='Stayed')
fig_3d.update_traces(marker=dict(size=5))
fig_3d.add_traces(go.Surface(x=x3d_range, y=y3d_range, z=pred, name='pred_surface'))
fig_3d.update_layout(width=900, margin={'r':45, 'l':35})
fig_3d.show()

#i think i should not put scatter_3d in there, the graph false

d:\python\projects\jupyter\kaggel_telco_customer\venv\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

d:\python\projects\jupyter\kaggel_telco_customer\venv\lib\site-packages\sklearn\base.py:450: UserWarning:

X does not have valid feature names, but SVR was fitted with feature names



In [ ]:
table_fig = go.Figure(data=[go.Table(
    header=dict(values=list(df.columns),
                fill_color='black', 
                align='left'),
    cells=dict(values=[df[c] for c in df.columns],
               fill_color='#2e2e52', 
               align='left'))
])
n=10   #number of columns to be displayed at a time
col_count = len(df.columns)
steps= [{'args': [{'header.values': [df.columns[k:k+n]],
                   'cells.values': [[df[col] for col in df.columns[k:k+n]]]
                  }], 
         'method': 'restyle'} for k in range((col_count-n+1))] 
                               
                               
table_fig.update_layout(sliders=[dict(active = 0,
                                minorticklen = 0,
                                steps = steps)])

table_fig.show()


In [ ]:

colors = {
    'background': '#111111',
    'text': '#7FDBFF',
    'width': 300
}

services_fig.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
contract_figure.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
churn_fig.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
linear_fig.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
fig_3d.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
churn_heatmap.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)
table_fig.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)

In [ ]:
app = Dash(__name__, title='Telco Churn Analysis')

app.layout = html.Div(
    style={'backgroundColor': colors['background']},
    
    children=[
        html.H1(
            children='Telco churn',
            style={
               'textAlign': 'center',
               'color': colors['text']
            }
        ),
        html.H4(children='Data used for analysis',
            style={
               'textAlign': 'center',
               'color': colors['text']
            }
        ),
        dcc.Graph(
            id='data',
            figure=table_fig
        ),

        html.Div(
            children='Telco Customer Churn data',
            style={
               'textAlign': 'center',
               'color': colors['text']
            }
        ),

        dcc.Graph(
            id='services-graph',
            figure=services_fig
        ),

        dcc.Graph(
            id='contract-fig',
            figure=contract_figure
        ),
        html.Div([
            html.Div([
                dcc.Dropdown(
                    [{
                        'label': html.Div(['Scatter plot']),
                        'value': 'Scatter plot', 
                    },
                    {
                        'label': html.Div(['Churn heatmap']),
                        'value': 'Heatmap'
                    }],
                    id='shown_distribution',
                    value='Scatter plot',
                    style=colors,
                ),
                dcc.Graph(id='churn-dist'),
            ], className='two columns'
            ),
            html.Div([        
                dcc.Dropdown(
                    ['Left 2D regression', 'Stayed 3D regression'],
                    id='shown_corr',
                    value='Left 2D regression',
                    style=colors
                ),
                dcc.Graph(id='correlation'),
            ], className='two columns'
            ),
        ], className='row')
    ]
)

    


@app.callback(
    Output('churn-dist', 'figure'),
    Input('shown_distribution', 'value')
)
def update_distr(shown_distr):
    if shown_distr == 'Scatter plot':
        return churn_fig
    else:
        return churn_heatmap

@app.callback(
    Output('correlation', 'figure'),
    Input('shown_corr', 'value')
)
def update_corr(shown_corr):
    if shown_corr == 'Left 2D regression':
        return linear_fig
    else:
        return fig_3d

app.css.append_css({
    'external_url': 'https://codepen.io/chriddyp/pen/bWLwgP.css'
})


In [ ]:
if __name__ == '__main__':
    app.run_server()

In [ ]:
charges

In [ ]:
%tb